# Utils and imports


In [64]:
#! pip install stanza --quiet
#import stanza
#from stanza import pipeline
#import io
import requests
import re
import sys

import pickle
import os
import json
#from google.colab import drive
import pprint
#from stanza.utils.conll import CoNLL
#drive.mount("/content/drive")
#stanza_path = "/content/drive/My Drive/stanza_data/"
#nlpforall_path = "/content/drive/My Drive/nlp4all/"
t = [i.strip() for i in open("/home/luca/Gits/nlp4all/nlp4all_web_app/texts/pavese_il_compagno/pavese_il_compagno.txt","r").readlines()]

# Sentence split



In [ ]:
s = """Lilí disse: «Viene giorno. Non mi piace!». E poi disse «Ancora una volta? Non voglio. Basta.». Infine, se ne andò. Piano. Come sempre, dicendo: «sei un pavido!»."""
def sentsplitter(s):
    s_count = 0
    htmlout = ""
    out = []
    gino = [i.span() for i in mspeech.finditer(s)] # get the indices of starts and ends of reported speech
    parts = [i for t in gino for i in t] # extract indices from tuples
    sents = []
    if 0 not in parts: # add index 0 to ranges
        parts.append(0)
    if len(s) not in parts:
        parts.append(len(s))
    parts = sorted(parts) # sorts the indices
    for i,part in enumerate(parts): # recreate sentences order
        try:
            sents.append(s[part:parts[i+1]])
        except IndexError: #handle index error 
            pass
    final_sents = []    
    for sid,sent in enumerate(sents):
        if not mspeech.search(sent): #handle non reported speech cases
            #print(sent)
            final_sents.append((sid,splitsent(sent))) # append index and sentences. Some sentences are lists
            
        else:
            new_s = [i for i in mspeech.split(sent) if i!= "" and i != None] # create new split reported speech sentence
            #print(new_s)
            try:
                if re.search(r"[.;:]", new_s[-1]): # if punctuation after angular brackets
                    start = new_s[0] 
                    middle = new_s[1]
                    end = "".join(new_s[2:])
                    new_middle = splitsent(middle)
                    if len(new_middle) >1:
                        start2 = new_middle.pop(0)
                        end2 = new_middle.pop(-1)
                        if new_middle == []: # new_middle is an empty list after popping start and end if it only contains two sentences 
                            final_sents.append((sid, [start + start2 +"»", "«" + end2 +end]))
                        else:  # if it is longer than two sentences
                            repsp2 = splitsent(middle) 
                            #print(repsp2)
                            new_middle2 = ["«"+i+"»" for i in repsp2[1:-1]  ] # recreate reported speech sentences with added angular brackets
                            new_s2 = [start  + repsp2[0] + "»"]
                            new_s2.extend(new_middle2)
                            new_s2.append(  "«" + repsp2[-1] +end)
                            new_s2 = (sid,new_s2)
                            final_sents.append(new_s2)
                    else:
                        final_sents.append((sid,[sent]))
                else:  # if punctuation NOT after angular brackets
                    final_sents.append((sid,[ ' '.join(x).strip()+"»" for x in zip(new_s[0::2], new_s[1::2])]))
            except Exception as e:
                print(new_s, e, i)
    return final_sents


## Gutenberb links and cleanup

In [ ]:
gut_urls = ["https://gutenberg.org/ebooks/25344.txt.utf-8", # The scarlet letter
            "https://gutenberg.org/files/174/174-0.txt"     # The picture of Dorian Gray
            ]


In [ ]:
def gut_cleaner(url):
  r = requests.get(url)
  r.encoding = "utf-8-sig"
  text = r.text
  s = re.search(r"\*\*+\s*START.*\*+", text ).span()[1]
  e = re.search(r"\*\*+\s*END.*\*+", text ).span()[0]
  return re.sub(r"\r\n", "\n" ,text[s:e].strip())
dtexts = {i:gut_cleaner(url) for i,url in enumerate(gut_urls)}

# Stanza 

In [ ]:
# nlp_en = stanza.Pipeline("en", dir=stanza_path, verbose = False , use_gpu=True) # wee need the dep parse
nlp_it = stanza.Pipeline("it", dir=stanza_path, processors="tokenize, pos, lemma, mwt", verbose = False , use_gpu=True )
nlp_it2 =  stanza.Pipeline("it", dir=stanza_path, processors="tokenize, pos, lemma, mwt", verbose = False , use_gpu=True, tokenize_pretokeniz =True )
#nlp_it = stanza.Pipeline("it", dir=stanza_path, processors="tokenize, pos, lemma", verbose = False , use_gpu=True )

# Nlp4All text processing functions

In [ ]:
import stanza
import sys
import os
import re
import json
import pickle
punctuation = set(""")⁄;(€!‘¨·£‰‐_§⁂∴<~«°¦%•¶`?\\—»‒№#.¡′※†₪‡¬☞’:+,[␠¤^{/¿¢‱”@}]=&–―₩‽-…"'>*“¥|$""")

def toksinsent(sent_, tokens = True):
    if tokens:
        return " ".join([i.text for i in sent_.tokens])
    else:
        return " ".join([i.text for i in sent_.words])

def stanza_annotation(doc_, css_info=""):

#### TODO: eliminate &nbsp at the beginning of the sentence 
    new_txt=f'<html><head>{css_info}<meta charset="UTF-8"></head><body>'
    nsent=1
    
    for sent in doc_.sentences:
        new_txt+="<span class='sentence' id='s" + str(nsent) +"'>"
        new_sent=""
        for tok in sent.tokens:
            try:
                if tok.text not in punctuation:
                    if len(tok.id) == 1:
                        tok_id = "-".join([str(i) for i in tok.id])
                        new_sent+=f"<span>&nbsp</span><span class='word' id='s{nsent}_w{tok_id}'>{tok.text}</span>"
                    else:
                        word = tok.to_dict()[0]
                        mwt_id = "-".join([str(i) for i in word["id"]])
                        mwt_text = word["text"]
                        new_sent+=f"<span>&nbsp</span><span class='mwt' id='s{nsent}_w{mwt_id}'>{mwt_text}</span>"
                        

                else:
                    tok_id = "-".join([str(i) for i in tok.id])
                    new_sent+=f"<span>&nbsp</span><span class='word' id='s{nsent}_w{tok_id}'>{tok.text}</span>"
            except Exception as e:
                print(tok.text, e)
                
        new_txt+= new_sent + "</span><span><br></span>" + "\n"
        nsent+=1
    return(new_txt + "</body><html>")



def generate_d_from_stanza(doc_):
  c = 1
  d = {}
  for sent in doc_.sentences:
    out = {}
    for d_temp in sent.to_dict():
      try:
        if "feats" in d_temp:
          features = [tuple(i.split("=")) for i in d_temp["feats"].split("|")]
          d_temp.pop("feats")
          for key,val in features:
            d_temp[key.lower()] = val
            d_temp["ismwt"] = False
          out[f"s{str(c)}_w{d_temp['id']}"]= d_temp
        elif isinstance(d_temp['id'], tuple):
          newid = "-".join([str(i) for i in d_temp['id']])
          d_temp["ismwt"] = True
          d_temp["sub_ids"] = d_temp["id"]
          out[f"s{str(c)}_w{newid}"] = d_temp
        else:
          d_temp["ismwt"] = False
          out[f"s{str(c)}_w{d_temp['id']}"] = d_temp
          
      except KeyError:
        print(d_temp)
    d["s"+str(c)] = out # modifies version
    # d["sent_"+str(c)] = out ù previous version 
    c += 1
  return d


In [ ]:
!pwd

/content


In [ ]:
pavdoc = pickle.load(open("/content/drive/MyDrive/nlp4all/texts/pavese_il_compagno.pkl","rb"))



In [ ]:
s = pavdoc.sentences[3]

def sent_types(sents_):
  out = {"int":[], "decl":[], "excl":[]}
  for s in sents_:
    if s.text.endswith("?"):
      out["int"].append(s.text)
    elif s.text.endswith("!"):
      out["excl"].append(s.text)
    else:
      out["decl"].append(s.text)
  return out

In [ ]:
doc = nlp_it2(open("/content/drive/MyDrive/nlp4all/texts/pavese_il_compagno.txt","r").read())

/usr/local/lib/python3.7/dist-packages/stanza/models/common/beam.py:86: UserWarning: __floordiv__ is deprecated, and its behavior will change in a future version of pytorch. It currently rounds toward 0 (like the 'trunc' function NOT 'floor'). This results in incorrect rounding for negative values. To keep the current behavior, use torch.div(a, b, rounding_mode='trunc'), or for actual floor division, use torch.div(a, b, rounding_mode='floor').
  prevK = bestScoresId // numWords


In [58]:
m = [m for m in mspeech.finditer(s)]
m[0].span()


(12, 42)

In [152]:
splitsent("E poi disse ")

[]

In [4]:
mspeech = re.compile(r"(«)([\w ?'’,!.;:]+)(»)([.:;?!])?")
sentend= re.compile(r"»[.;:][ \n\r]")
msent = re.compile(""" ?([\w"']+[”»’–]?[?.!;:][”»’–]? ?)""")

def splitsent(in_s):
    text = in_s
    out= []
    if msent.search(text):
        t = msent.split(text)
        out.extend([ ' '.join(x).strip() for x in zip(t[0::2], t[1::2]) ])
    else:
        return [text.strip()]
    return out

In [44]:
s = """Lilí disse: «Viene giorno. Non mi piace!». E poi disse «Ancora una volta? Non voglio. Basta.». Infine, se ne andò. Piano. Come sempre, dicendo: «sei un pavido!»."""
def sentsplitter(s):
    s_count = 0
    htmlout = ""
    out = []
    gino = [i.span() for i in mspeech.finditer(s)] # get the indices of starts and ends of reported speech
    parts = [i for t in gino for i in t] # extract indices from tuples
    sents = []
    if 0 not in parts: # add index 0 to ranges
        parts.append(0)
    if len(s) not in parts:
        parts.append(len(s))
    parts = sorted(parts) # sorts the indices
    for i,part in enumerate(parts): # recreate sentences order
        try:
            sents.append(s[part:parts[i+1]])
        except IndexError: #handle index error 
            pass
    final_sents = []    
    for sid,sent in enumerate(sents):
        if not mspeech.search(sent): #handle non reported speech cases
            #print(sent)
            final_sents.append((sid,splitsent(sent))) # append index and sentences. Some sentences are lists
            
        else:
            new_s = [i for i in mspeech.split(sent) if i!= "" and i != None] # create new split reported speech sentence
            #print(new_s)
            try:
                if re.search(r"[.;:]", new_s[-1]): # if punctuation after angular brackets
                    start = new_s[0] 
                    middle = new_s[1]
                    end = "".join(new_s[2:])
                    new_middle = splitsent(middle)
                    if len(new_middle) >1:
                        start2 = new_middle.pop(0)
                        end2 = new_middle.pop(-1)
                        if new_middle == []: # new_middle is an empty list after popping start and end if it only contains two sentences 
                            final_sents.append((sid, [start + start2 +"»", "«" + end2 +end]))
                        else:  # if it is longer than two sentences
                            repsp2 = splitsent(middle) 
                            #print(repsp2)
                            new_middle2 = ["«"+i+"»" for i in repsp2[1:-1]  ] # recreate reported speech sentences with added angular brackets
                            new_s2 = [start  + repsp2[0] + "»"]
                            new_s2.extend(new_middle2)
                            new_s2.append(  "«" + repsp2[-1] +end)
                            new_s2 = (sid,new_s2)
                            final_sents.append(new_s2)
                    else:
                        final_sents.append((sid,[sent]))
                else:  # if punctuation NOT after angular brackets
                    final_sents.append((sid,[ ' '.join(x).strip()+"»" for x in zip(new_s[0::2], new_s[1::2])]))
            except Exception as e:
                print(new_s, e, i)
    return final_sents

In [36]:
[i for i in mspeech.split(t[69]) if i!= "" and i != None][-1] 

'»'

In [29]:
mspeech.split(t[69])

['', '«', 'Ma qualcosa lo fai.', '»', None, '']

In [33]:
t[68:78]

['Allora dissi che a ciascuno il suo mestiere e che Amelio era stato piú in gamba di me e ch’io vivevo sopra il corso e praticavo solamente i tabacchi e i ciclisti.',
 '«Ma qualcosa lo fai.»',
 'Non ci pensavo, e lei mi disse che suonavo la chitarra. «Suoni bene?»',
 '«Chi sa.»',
 '«Una sera ti voglio sentire.»',
 'Allora bisognava rivederci, le dissi ridendo.',
 '«Si capisce» mi disse.',
 'Ci sedemmo al caffè e cosí potei vederla bene in faccia. Quando parlavo, mi guardava dentro gli occhi. Io pensavo alle gambe di Amelio.',
 'Per capire se anche lei le aveva viste, le raccontai della mattina. Fece una smorfia e chiuse gli occhi; lasciò che dicessi. Non avevo finito che mi mise una mano sul braccio e disse in fretta:',
 '«Dobbiamo aiutarlo. Non può piú lavorare.»']

In [62]:
gino = [sentsplitter(text) for text in t]

In [63]:
gino

[[(0,
   ['Mi dicevano Pablo perché suonavo la chitarra.',
    'La notte che Amelio si ruppe la schiena sulla strada di Avigliana, ero andato con tre o quattro a una merenda in collina – mica lontano, si vedeva il ponte – e avevamo bevuto e scherzato sotto la luna di settembre, finché per via del fresco ci toccò cantare al chiuso.',
    'Allora le ragazze si eran messe a ballare.',
    'Io suonavo – Pablo qui, Pablo là –ma non ero contento, mi è sempre piaciuto suonare con qualcuno che capisca, invece quelli non volevano che gridare piú forte.',
    'Toccai ancora la chitarra andando a casa e qualcuno cantava.',
    'La nebbia mi bagnava la mano.',
    'Ero stufo di quella vita.'])],
 [(0,
   ['Adesso che Amelio era finito all’ospedale, non avevo con chi dir la mia e sfogarmi.',
    'Si sapeva ch’era inutile andarlo a trovare perché gridava giorno e notte e bestemmiava, e non conosceva piú nessuno.',
    'Andammo a vedere la moto ch’era ancora nel fosso, contro un paracarro.',
    'S’e

In [9]:
sample = '«Ci sono».\nSe ne andò nella nebbia.'
def sent_tokenizer(text):
    out = []
    msent = re.compile(""" ?([\w"']+[”»’–]?[?.!;:][”»’–]? ?)""")
    text = re.split(r"[\r\n]+", text)
    mspeech = re.compile(r"(«)([\w ?'’,!.;:]+)(»)")
    rep_speech= []
    for sent in text:
        if mspeech.search(sent):
            out.append(f"________{sent}_____________")
      #  rs = [i for i in mspeech.split(sent) if i not in ["«»"]]
      #  temp = []
      #  for t in rs:
      #    ttemp = msent.split(t)
      #    temp.extend([ ' '.join(x) for x in zip(ttemp[0::2], ttemp[1::2]) ])

      #  out.extend([f"«{i}" for i in temp])
        else:
            temp = msent.split(sent)
            out.extend([ ' '.join(x) for x in zip(temp[0::2], temp[1::2]) ])
        
   
  # joined =  [ ' '.join(x) for x in zip(split[0::2], split[1::2]) ]
    return out
  # print("\n".join(sorted(sent_tokenizer(t), key=  lambda x: len(x), reverse = True)))
sent_tokenizer(t)

['Mi dicevano Pablo perché suonavo la chitarra. ',
 'La notte che Amelio si ruppe la schiena sulla strada di Avigliana, ero andato con tre o quattro a una merenda in collina – mica lontano, si vedeva il ponte – e avevamo bevuto e scherzato sotto la luna di settembre, finché per via del fresco ci toccò cantare al chiuso. ',
 'Allora le ragazze si eran messe a ballare. ',
 'Io suonavo – Pablo qui, Pablo là –ma non ero contento, mi è sempre piaciuto suonare con qualcuno che capisca, invece quelli non volevano che gridare piú forte. ',
 'Toccai ancora la chitarra andando a casa e qualcuno cantava. ',
 'La nebbia mi bagnava la mano. ',
 'Ero stufo di quella vita.',
 'Adesso che Amelio era finito all’ospedale, non avevo con chi dir la mia e sfogarmi. ',
 'Si sapeva ch’era inutile andarlo a trovare perché gridava giorno e notte e bestemmiava, e non conosceva piú nessuno. ',
 'Andammo a vedere la moto ch’era ancora nel fosso, contro un paracarro. ',
 'S’era spaccata la forcella, saltata la ruo

In [ ]:
rep_speech = re.compile(r"(«)([\w ?'’,!.;:]+)(»)")
text = re.split(r"[\r\n]+", t)
for sent in text:
  if rep_speech.search(sent):
    print(rep_speech.search(sent).group(2))

Sono Linda,
Che chitarra.
Siamo andati a vedere la moto
Una moto si aggiusta
Senti
Chiudi, è freddo.
Fumi forte?
Questa è la prima. Le finisco di notte.
Io da quel giorno la chitarra non l’ho piú portata a spasso
Anche da soli non è allegro
Se suonassi per vivere, capiresti qualcosa
Fa male?
Ti va bene
E non vai piú nei prati?
Mi dev’essere successo qualcosa. Non mi va piú la compagnia. Neanche il negozio non mi piace. Sarà che ho voglia di far niente, ma non credo. Tanta gente c’è al mondo, e tutti fanno, tutti vivono. Tu che eri sempre in movimento lo puoi dire. Serve a qualcosa stare in casa?
Ma ce l’hai la ragazza?
Cos’importa? La pianti e stai meglio.
Dipende.
Non ti hanno piú portato il mazzo
Ti va bene se vengo a quest’ora?
Vai di là, prendi un bicchiere
Non devo mica camminare.
Non bere troppo
La questione è carrozza o stampelle
Cosa dicono i medici?
Per loro...
Hai freddo
Non vi siete visti?
So che l’hanno sgessato
Preferisce se vanno delle ragazze a trovarlo...
Amelio sta mal

In [ ]:
m.split(sample)

['«Ci', 'sono».\n', 'Se ne andò nella nebbia.']

In [ ]:
"aweqwrqttq"[1::2]

'wqrtq'

In [ ]:
[i for i in zip(m.split(sample)[0::2], m.split(sample)[1::2])]

[('«Ci', 'sono».\n')]

In [ ]:
print(sample)

«Ci sono».
Se ne andò nella nebbia.


In [ ]:
sent_types(doc.sentences)["int"]

['Amelio viveva per questo – tutto il giorno provava motori – come farebbe adesso a vivere?',
 'Vale la pena la chitarra per divertire quattro stupidi che si fanno trovare la sera nei prati?',
 'Potevo dirgli ch’ero stufo della vita che facevo e che avrei preferito suonare per vivere?',
 'Che il mondo era grande e volevo cambiare? girarlo e cambiare?',
 'Tanta gente c’è al mondo, e tutti fanno, tutti vivono. Tu che eri sempre in movimento lo puoi dire. Serve a qualcosa stare in casa?»\n«Ma ce l’hai la ragazza?»\n«Cos’importa? La pianti e stai meglio.»\n«Dipende.»\nPerché facevo quei discorsi proprio con lui che era uno storpio?',
 'Allora mi vergognavo di aver detto che avrei fatto, avrei cercato, avrei girato, perché che cosa gl’importava tutto questo a lui ch’era uno storpio, inchiodato nel letto?',
 'Cosa serviva l’ospedale adesso, che ci tenevano la gente tanto tempo e non guariva?',
 'C’è qualcuno che ha fatto tanto di rendergli un soldo?']

In [ ]:
nlp_en("Going to school is difficult")

[
  [
    {
      "id": 1,
      "text": "Going",
      "lemma": "go",
      "upos": "VERB",
      "xpos": "VBG",
      "feats": "VerbForm=Ger",
      "head": 5,
      "deprel": "csubj",
      "start_char": 0,
      "end_char": 5,
      "ner": "O"
    },
    {
      "id": 2,
      "text": "to",
      "lemma": "to",
      "upos": "ADP",
      "xpos": "IN",
      "head": 3,
      "deprel": "case",
      "start_char": 6,
      "end_char": 8,
      "ner": "O"
    },
    {
      "id": 3,
      "text": "school",
      "lemma": "school",
      "upos": "NOUN",
      "xpos": "NN",
      "feats": "Number=Sing",
      "head": 1,
      "deprel": "obl",
      "start_char": 9,
      "end_char": 15,
      "ner": "O"
    },
    {
      "id": 4,
      "text": "is",
      "lemma": "be",
      "upos": "AUX",
      "xpos": "VBZ",
      "feats": "Mood=Ind|Number=Sing|Person=3|Tense=Pres|VerbForm=Fin",
      "head": 5,
      "deprel": "cop",
      "start_char": 16,
      "end_char": 18,
      "ner": "O"
   

In [ ]:
doc.sentences[73].text

'“Not send it anywhere?'

In [ ]:
sent = doc.sentences[1]
token = sent.tokens[1]


{'deprel': 'root',
 'end_char': 36,
 'feats': 'Number=Sing',
 'head': 0,
 'id': 2,
 'lemma': 'Oscar',
 'ner': 'B-PERSON',
 'start_char': 31,
 'text': 'Oscar',
 'upos': 'PROPN',
 'xpos': 'NNP'}

In [ ]:
def stanza_annotation(doc_, css_info=""):

#### TODO: eliminate &nbsp at the beginning of the sentence 
    new_txt=f'<html><head>{css_info}<meta charset="UTF-8"></head><body>'
    nsent=1
    
    for sent in doc_.sentences:
      new_txt+="<span class='sentence' id='s" + str(nsent) +"'>"
      new_sent=""
      for tok in sent.words:
        if tok.pos != "PUNCT":
          new_sent+=f"<span>&nbsp</span><span class='word' id='s{nsent}_w{tok.id}'>{tok.text}</span>"
        else:
          new_sent+=f"<span class='word' id='s{nsent}_w{tok.id}'>{tok.text}</span>"

      new_txt+= new_sent + "</span><span><br></span>" + "\n"
      nsent+=1
    return(new_txt + "</body><html>")




def generate_d_from_stanza(doc_):
  c = 1
  d = {}
  for sent in doc_.sentences:
    out = {}
    for d_temp in sent.to_dict():
      try:
        if "feats" in d_temp:
          features = [tuple(i.split("=")) for i in d_temp["feats"].split("|")]
          for key,val in features:
            d_temp[key.lower()] = val
          out[f"s{str(c)}_w{d_temp['id']}"]= d_temp
        else:
          out[f"s{str(c)}_w{d_temp['id']}"] = d_temp
      except KeyError:
        print(d_temp)
    d["s"+str(c)] = out # modifies version
    # d["sent_"+str(c)] = out ù previous version 
    c += 1
  return d


In [ ]:
doc = nlp_en(open("/content/drive/MyDrive/nlp4all/texts/ataleoftwocities/ataleoftwocities.txt").read())
pickle.dump(doc,open("/content/drive/MyDrive/nlp4all/texts/ataleoftwocities/ataleoftwocities.pkl", "wb"))
with open("/content/drive/MyDrive/nlp4all/texts/ataleoftwocities/ataleoftwocities.html", "w", encoding="utf8") as html_out:
  html_out.write(stanza_annotation(doc))
json.dump(generate_d_from_stanza(doc), open("/content/drive/MyDrive/nlp4all/texts/ataleoftwocities/ataleoftwocities.json", "w", encoding="utf8"))

In [ ]:
with open() stanza_annotation(doc)

'<html><head><meta charset="UTF-8"></head><body><span class=\'sentence\' id=\'s1\'><span>&nbsp</span><span class=\'word\' id=\'s1_w1\'>Mi</span><span>&nbsp</span><span class=\'word\' id=\'s1_w2\'>dicevano</span><span>&nbsp</span><span class=\'word\' id=\'s1_w3\'>Pablo</span><span>&nbsp</span><span class=\'word\' id=\'s1_w4\'>perché</span><span>&nbsp</span><span class=\'word\' id=\'s1_w5\'>suonavo</span><span>&nbsp</span><span class=\'word\' id=\'s1_w6\'>la</span><span>&nbsp</span><span class=\'word\' id=\'s1_w7\'>chitarra</span><span class=\'word\' id=\'s1_w8\'>.</span></span><span><br></span>\n<span class=\'sentence\' id=\'s2\'><span>&nbsp</span><span class=\'word\' id=\'s2_w1\'>La</span><span>&nbsp</span><span class=\'word\' id=\'s2_w2\'>notte</span><span>&nbsp</span><span class=\'word\' id=\'s2_w3\'>che</span><span>&nbsp</span><span class=\'word\' id=\'s2_w4\'>Amelio</span><span>&nbsp</span><span class=\'word\' id=\'s2_w5\'>si</span><span>&nbsp</span><span class=\'word\' id=\'s2_w6\

# Old and Alia



In [ ]:
with open("/content/drive/MyDrive/nlp4all/treasure_island_short.txt") as infile:
  processed = nlp_en(infile.read())

import pickle
pickle.dump(processed, open("/content/drive/MyDrive/nlp4all/treasure_island_short.pkl", "wb"))

In [ ]:
import pickle
processed = pickle.load(open("/content/drive/MyDrive/nlp4all/treasure_island_short.pkl", "rb"))

In [ ]:
sample_it_url = "http://www.gutenberg.org/cache/epub/18456/pg18456.txt" # Pirandello, Enrico 4

def clean_text_from_gutenberg(a_url):
  r  = requests.get(a_url)
  r.encoding = "utf-8-sig"
  t = r.text
  t = re.sub("\r", "\n", t)
  t = re.sub(r"\n+", r"\n",t)
  start = re.search(r"\*\*\* START OF THIS PROJECT GUTENBERG EBOOK.* \*\*\*", t).span()[1]
  end = re.search("End of the Project Gutenberg EBook of", t).span()[0]
  return t[start:end] 

raw_pirandello = clean_text_from_gutenberg(sample_it_url).strip()
# processed_pirandello = nlp_it(raw_pirandello)

In [ ]:
small_raw = re.sub(r"([A-zè,])\n([,èA-z])",r"\1 \2", raw_pirandello[423:50000])
small_raw = re.sub(r"_[ \.\(\)\,\!;:A-zòàìùéè]+\._", "",small_raw)
small_doc = nlp_it(small_raw)

In [ ]:
def stanza_annotation(doc_):

#### TODO: eliminate &nbsp at the beginning of the sentence 
    new_txt='<html><head><meta charset="UTF-8"></head><body>'
    nsent=1
    
    for sent in doc_.sentences:
      new_txt+="<span class='sentence' id='s" + str(nsent) +"'>"
      new_sent=""
      for tok in sent.words:
        if tok.pos != "PUNCT":
          new_sent+=f"<span>&nbsp</span><span class='word' id='s{nsent}_w{tok.id}'>{tok.text}</span>"
        else:
          new_sent+=f"<span class='word' id='s{nsent}_w{tok.id}'>{tok.text}</span>"

      new_txt+= new_sent + "</span><span><br></span>" + "\n"
      nsent+=1
    return(new_txt + "</body><html>")

In [ ]:
def generate_d_from_stanza(doc_):
  c = 1
  d = {}
  for sent in doc_.sentences:
    out = []
    for d_temp in sent.to_dict():
      if "feats" in d_temp:
        features = [tuple(i.split("=")) for i in d_temp["feats"].split("|")]
        for key,val in features:
          d_temp[key] = val
        out.append(d_temp)
      else:
        out.append(d_temp)
    d["s"+str(c)] = out # modifies version
    # d["sent_"+str(c)] = out ù previous version 
    c += 1
  return d


In [ ]:
some_sents = [a.text for a in  processed.sentences[:10]]

In [ ]:
reprocessed = nlp_en("\n".join(some_sents))

In [ ]:
l =  []
poses = ["NOUN", "VERB", "ADJ", "AUX"]
for i,s in enumerate(reprocessed.sentences, 1):
  for j,t in enumerate(s.words, 1):
    try:
      feats = {k.split("=")[0]:k.split("=")[1]  for k in t.feats.split('|')}
      feats = "\t".join([i for i in feats.values()])
      if t.upos in poses:
        l.append(f"s{i}_w{j}\t{t.text}\t{t.lemma}\t{t.upos}\t{feats}" )
    except AttributeError:
      pass

In [ ]:
with open("/content/drive/MyDrive/nlp4all/small_treasure_island_feats.csv", "w") as outfile:
  for line in l:
    outfile.write(line +  "\n")

In [ ]:
stanza_annotation(reprocessed)

'<html><head><meta charset="UTF-8"></head><body><span class=\'sentence\' id=\'s1\'><span>&nbsp</span><span class=\'word\' id=\'s1_w1\'>The</span><span>&nbsp</span><span class=\'word\' id=\'s1_w2\'>Last</span><span>&nbsp</span><span class=\'word\' id=\'s1_w3\'>of</span><span>&nbsp</span><span class=\'word\' id=\'s1_w4\'>the</span><span>&nbsp</span><span class=\'word\' id=\'s1_w5\'>Blind</span><span>&nbsp</span><span class=\'word\' id=\'s1_w6\'>Man</span><span>&nbsp</span><span class=\'word\' id=\'s1_w7\'>MY</span><span>&nbsp</span><span class=\'word\' id=\'s1_w8\'>curiosity</span><span class=\'word\' id=\'s1_w9\'>,</span><span>&nbsp</span><span class=\'word\' id=\'s1_w10\'>in</span><span>&nbsp</span><span class=\'word\' id=\'s1_w11\'>a</span><span>&nbsp</span><span class=\'word\' id=\'s1_w12\'>sense</span><span class=\'word\' id=\'s1_w13\'>,</span><span>&nbsp</span><span class=\'word\' id=\'s1_w14\'>was</span><span>&nbsp</span><span class=\'word\' id=\'s1_w15\'>stronger</span><span>&nbs

In [ ]:
# import pickle

# pickle.dump(small_doc, open("/content/drive/MyDrive/nlp4all/small_doc.pkl", "wb"))

In [ ]:
# with  open(nlpforall_path + "small_sample_pirandello_25_11_2020.html", "w") as htmlout:
#   htmlout.write(stanza_annotation(small_doc))

In [ ]:
# def generate_json(doc_):
#   c = 1
#   d = {}
#   for sent in doc_.sentences:
#     out = []
#     for d_temp in sent.to_dict():
#       if "feats" in d_temp:
#         features = [tuple(i.split("=")) for i in d_temp["feats"].split("|")]
#         for key,val in features:
#           d_temp[key] = val
#         out.append(d_temp)
#       else:
#         out.append(d_temp)
#     d["sent_"+str(c)] = out
#     c += 1
#   return d

In [ ]:
generate_json(small_doc)

{'sent_1': [{'Definite': 'Ind',
   'Gender': 'Fem',
   'Number': 'Sing',
   'PronType': 'Art',
   'feats': 'Definite=Ind|Gender=Fem|Number=Sing|PronType=Art',
   'id': 1,
   'lemma': 'uno',
   'misc': 'start_char=0|end_char=3',
   'text': 'una',
   'upos': 'DET',
   'xpos': 'RI'},
  {'Gender': 'Fem',
   'Number': 'Sing',
   'feats': 'Gender=Fem|Number=Sing',
   'id': 2,
   'lemma': 'villa',
   'misc': 'start_char=4|end_char=9',
   'text': 'villa',
   'upos': 'NOUN',
   'xpos': 'S'},
  {'Gender': 'Fem',
   'Number': 'Sing',
   'feats': 'Gender=Fem|Number=Sing',
   'id': 3,
   'lemma': 'solitario',
   'misc': 'start_char=10|end_char=19',
   'text': 'solitaria',
   'upos': 'ADJ',
   'xpos': 'A'},
  {'Gender': 'Fem',
   'Number': 'Sing',
   'feats': 'Gender=Fem|Number=Sing',
   'id': 5,
   'lemma': 'campagna',
   'misc': 'start_char=26|end_char=34',
   'text': 'campagna',
   'upos': 'NOUN',
   'xpos': 'S'},
  {'Gender': 'Fem',
   'Number': 'Sing',
   'feats': 'Gender=Fem|Number=Sing',
   '

In [ ]:
# sent = small_doc.sentences[0]
# stanza_annotation(small_doc)

In [ ]:
# import json

# json.dump(generate_json(small_doc), open(nlpforall_path + "small_sample_pirandello_25_11_2020.json", "w"))

In [ ]:
################################################################################################################
# MZ 08/05/2020
# (0) prende in input un file di testo e il path di un file CSS
# (1) tagga ogni paragrafo con un <div> con classe paragraph e id pN dove N è un numero da 1 al max paragrafi
# (2) mette html, head e body; inserisce il tag di style 
# (3) restituisce la string html
################################################################################################################
def tagging(text_,css_filename):
    text_out=""
    lines = text_.split()
    n=len(lines)
    print(f"{n} lines have been read")
    s=lines
    
    paragraph=''
    nparagraph=1
    for l in lines:
        if l.strip()=='' and paragraph!='' :
            text_out+= f"\n<div class='paragraph' id='par{nparagraph}'>{paragraph}</div>"
            paragraph=''
            nparagraph+=1
        else:
            l=l.strip()
            paragraph=f"{paragraph} {l}".strip()
    
    print(f"{nparagraph} paragraphs")
    
    text_out=f"<html>\n<head>\n<link rel='stylesheet' href='{css_filename}'>\n</head>\n<body>{text_out}\n</body>\n</html>"
    return(text_out)




In [ ]:
def parse(doc_):

    d=doc_.to_dict()
    
    new_list=[]
    sentence_id=0
    
    for sentence in d:
        for word in sentence:
            new_word={}
            new_word['sent_id']=f"s{sentence_id}"; sentence_id+=1
            token_id=word['id']; new_word['tok_id']=f"t{token_id}"
            new_word['text']=word['text']
            new_word['lemma']=word['lemma']
            new_word['upos']=word['upos']
            
            new_list.append(new_word)
  
    return(new_list)

In [ ]:
# stanza_annotation(processed_pirandello, raw_pirandello)
stanza_annotation(small_doc, small_raw)

"<span class='sentence' id='sent1'><span class='word' pos=DET id='w1'>una</span><span>&nbsp</span><span class='word' pos=NOUN id='w2'>villa</span><span>&nbsp</span><span class='word' pos=ADJ id='w3'>solitaria</span><span>&nbsp</span><span class='word' pos=ADP id='w4'>di</span><span>&nbsp</span><span class='word' pos=DET id='w5'>la</span><span>&nbsp</span><span class='word' pos=NOUN id='w6'>campagna</span><span>&nbsp</span><span class='word' pos=ADJ id='w7'>umbra</span><span>&nbsp</span><span class='word' pos=ADP id='w8'>a</span><span>&nbsp</span><span class='word' pos=DET id='w9'>i</span><span>&nbsp</span><span class='word' pos=DET id='w10'>nostri</span><span>&nbsp</span><span class='word' pos=NOUN id='w11'>giorni</span><span>&nbsp</span><span class='word' pos=PUNCT id='w12'> .</span><span>&nbsp</span><span class='word' pos=PUNCT id='w13'> _</span><span>&nbsp</span><span class='word' pos=PUNCT id='w14'> (</span><span>&nbsp</span><span class='word' pos=NOUN id='w15'>Salone</span><span>&

In [ ]:
# from google.colab import drive
# drive.mount("/content/drive")
# import json
# # json.dump(text_processed.to_dict(), open("drive/My Drive/nlp4all/out_sample.json", "w", encoding="utf8"))
# # json.dump(parse(text_processed), open("drive/My Drive/nlp4all/out_sample_parsed.json", "w"))
# with open("drive/My Drive/nlp4all/out_sample.html" , "w", encoding= "utf8" ) as out_sample:
#           out_sample.write(stanza_annotation(processed_pirandello, raw_pirandello))

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
# t  = requests.get("https://www.gutenberg.org/files/63469/63469-0.txt").text
# Peter Pan
r  = requests.get("https://www.gutenberg.org/files/16/16-0.txt")
r.encoding = "utf-8-sig"
t = r.text
t = re.sub("\r", "\n", t)
start = re.search(r"\*\*\* START OF THIS PROJECT GUTENBERG EBOOK PETER PAN \*\*\*", t).span()[1]
end = re.search("End of the Project Gutenberg EBook of", t).span()[0]
text = t[start:end]
nlp_en = stanza.Pipeline("en", processors="tokenize,pos,lemma")
text_processed = en_nlp(text)

AttributeError: 'NoneType' object has no attribute 'span'

## Import or generate json


In [ ]:
import json

imported_json = json.load(open(nlpforall_path + "small_sample_pirandello.json"))


In [ ]:
generated_json = generate_json(small_doc)  

In [ ]:
len(generated_json)

873

In [ ]:
def how_many_pos(data, pos):
  """- Data: is a the dictionary/json that is the output of stanza.
     - pos: is the return of a function in the frontend (wxpython) as a string
     """
  out = {}
  for sentid,list_of_ds in data.items():
    out[sentid] = []
    for dict_ in list_of_ds:
      if  dict_["upos"] == pos:
         out[sentid].append(dict_["id"])
  c = 0
  for listids in out.values():
    c+= len(listids)
  return c, out

In [ ]:
generated_json['sent_830']

[{'id': 1,
  'lemma': 'no...',
  'misc': 'start_char=37614|end_char=37619',
  'text': 'No...',
  'upos': 'INTJ',
  'xpos': 'I'},
 {'id': 2,
  'lemma': 'da',
  'misc': 'start_char=37620|end_char=37622',
  'text': 'da',
  'upos': 'ADP',
  'xpos': 'E'},
 {'feats': 'Number=Sing|Person=1|PronType=Prs',
  'id': 3,
  'lemma': 'me',
  'misc': 'start_char=37623|end_char=37625',
  'text': 'me',
  'upos': 'PRON',
  'xpos': 'PC'},
 {'id': 4,
  'lemma': ',',
  'misc': 'start_char=37625|end_char=37626',
  'text': ',',
  'upos': 'PUNCT',
  'xpos': 'FF'},
 {'id': 5,
  'lemma': 'no..',
  'misc': 'start_char=37627|end_char=37631',
  'text': 'no..',
  'upos': 'INTJ',
  'xpos': 'I'},
 {'id': 6,
  'lemma': '.',
  'misc': 'start_char=37631|end_char=37632',
  'text': '.',
  'upos': 'PUNCT',
  'xpos': 'FS'}]

In [ ]:
how_many_pos(generated_json, "VERB")

(965,
 {'sent_1': [17, 21],
  'sent_10': [5, 8],
  'sent_100': [],
  'sent_101': [1],
  'sent_102': [1, 7],
  'sent_103': [2, 9, 12],
  'sent_104': [],
  'sent_105': [5, 10, 16],
  'sent_106': [],
  'sent_107': [],
  'sent_108': [],
  'sent_109': [],
  'sent_11': [5],
  'sent_110': [],
  'sent_111': [],
  'sent_112': [7],
  'sent_113': [1],
  'sent_114': [4, 10],
  'sent_115': [5, 7, 21],
  'sent_116': [21],
  'sent_117': [],
  'sent_118': [13, 19, 21, 27],
  'sent_119': [8, 12, 14],
  'sent_12': [],
  'sent_120': [2, 6],
  'sent_121': [6],
  'sent_122': [9, 11],
  'sent_123': [7, 10],
  'sent_124': [2, 5],
  'sent_125': [13],
  'sent_126': [1, 7],
  'sent_127': [9],
  'sent_128': [3],
  'sent_129': [],
  'sent_13': [],
  'sent_130': [4, 9, 13, 17, 22, 23],
  'sent_131': [],
  'sent_132': [],
  'sent_133': [1, 2],
  'sent_134': [1, 2],
  'sent_135': [5],
  'sent_136': [],
  'sent_137': [3],
  'sent_138': [2, 12, 21],
  'sent_139': [3, 6],
  'sent_14': [5],
  'sent_140': [1],
  'sent_14

In [ ]:
def get_words(data, pos, features):
  """- Data: is a the dictionary/json that is the output of stanza.
     - pos: is the output of the Get_value() function in wxpython as a string
     - 
     """
  
  for sent in data:



{'sent_1': [{'feats': 'Mood=Ind|Number=Sing|Person=1|Tense=Imp|VerbForm=Fin',
   'id': 1,
   'lemma': 'sapere',
   'misc': 'start_char=3482|end_char=3488',
   'text': 'Sapevo',
   'upos': 'VERB',
   'xpos': 'V'},
  {'feats': 'Definite=Ind|Gender=Masc|Number=Sing|PronType=Art',
   'id': 2,
   'lemma': 'uno',
   'misc': 'start_char=3489|end_char=3491',
   'text': 'un',
   'upos': 'DET',
   'xpos': 'RI'},
  {'feats': 'Gender=Masc|Number=Sing',
   'id': 3,
   'lemma': 'corno',
   'misc': 'start_char=3492|end_char=3497',
   'text': 'corno',
   'upos': 'NOUN',
   'xpos': 'S'},
  {'feats': 'Number=Sing|Person=1|PronType=Prs',
   'id': 4,
   'lemma': 'io',
   'misc': 'start_char=3498|end_char=3500',
   'text': 'io',
   'upos': 'PRON',
   'xpos': 'PE'}]}

## Avanzi


In [ ]:
################################################################################################################
# MZ 08/05/2020
# (0) prende in input una stringa (senza TAG HTML)
# (1) la passa al processore stanza
# (2) per ogni frase mette un tag <span class="sentence" id="sent#">
# (3) per ogni token mette un tag <span class="token" id="tok#">
################################################################################################################

# def stanza_annotation (doc_from_stanza, original_txt):
#   # TODO:  ling features should not be spans attributes anymore. 
#     new_txt=""
#     nsent=1

#     for sent in doc_from_stanza.sentences:
#         # identifies the first characher of the first tokens and the last char of the last token 
#         # sent_start = int(sent.tokens[0].misc.split('|')[0].split('=')[1])
#         # sent_end = int(sent.tokens[len(sent.tokens)-1].misc.split('|')[1].split('=')[1])
        
#         # sentence=original_txt[sent_start:sent_end]
        
#         new_sent=""
#         for tok in sent.words:
#             #tok_start=int(tok.misc.split('|')[0].split('=')[1])
#             #tok_end=int(tok.misc.split('|')[1].split('=')[1])
#             # txt[tok_start:tok_end]
#             token_id=tok.id
#             content=tok.text
#             # space= ' ' if tok.upos=="PUNCT" else '' 
#             # new_sent+=f"<span class='word' pos={tok.upos} id='w{token_id}'>{space}{content}</span><span>&nbsp</span>"
#             if tok.pos != "PUNCT":
#               new_sent+=f"</span><span>&nbsp<span class='word' id='{token_id}'>{content}</span>"
#             else: 
#               new_sent+=f"<span class='word' id='{token_id}'>{content}</span>"

#         new_txt+=f"<span class='sentence' id='sent_{nsent}'>{new_sent}</span><span><br></span>"
#         nsent+=1


#     return(new_txt)

In [ ]:
# Sample text from one of Barilli's novels

sample_barilli = """Restaurare nel civile consorzio il senso morale parrà necessario a chi
pensa; e necessario veder cominciare la restaurazione dai capi, dai capi
della famiglia, dai capi della società, donde l'autorità deriva, donde
gli esempi si spargono. Ma noi non faremo niente senza virtù private,
senza idealità che le informino, scaldandone la buona semente nei cuori.
Tanto io credo, «e creder credo il vero». Per ritornare al libro che ti
offro, esso sarà giudicato come vorrà essere; anzi diciamo pure,
pronosticando, che non sarà giudicato affatto. Viviamo in un paese di
gente savia e prudente, che aspetta di fuori sentenze ed oracoli, mode,
predizioni del tempo ed almanacchi. Mi preme soltanto che il libro sia
sentito da coloro che lo leggeranno. Da ventimila, dice l'amico editore,
sperando: da venti, dico io, già molto ambizioso, se penso ai
venticinque di cui si contentava il Manzoni: nel fatto, levando tutti
gli zeri, me ne bastano due."""
barillinlp = nlp_it(sample_barilli)